The STM32 SVD files are located at:

\<CubeIDE Directory\>\STM32CubeIDE\plugins\com.st.stm32cube.ide.mcu.productdb.debug_xxxxxx\resources\cmsis\STMicroelectronics_CMSIS_SVD\

Copy the `.SVD` file to the same directory as this notebook.

Change the `model` according to the model.

Then run all cells, and a python file will be generated, named by the model. Import it in your application code.

In [75]:
model = "n657"

# if True, remove SEC_ and prefix NSEC_ for others
secure = False

In [76]:
import xml.etree.ElementTree as ET
import re
import copy

In [77]:
def get_description(node):
    if node.find("description") is None:
        desc = ""
    else:
        desc = node.find("description").text
        desc = desc.replace("\n", ". ", 1)
    return " ".join(desc.split())

In [78]:
root = ET.parse(f"./stm32{model}.svd").getroot().find("peripherals")
for child in root:
    print(child.tag, child.find("name").text, child.attrib)

peripheral ADC1 {}
peripheral ADC1_S {'derivedFrom': 'ADC1'}
peripheral ADC2 {'derivedFrom': 'ADC1'}
peripheral ADC2_S {'derivedFrom': 'ADC1'}
peripheral ADC12 {}
peripheral ADC12_S {'derivedFrom': 'ADC12'}
peripheral ADF {}
peripheral ADF_S {'derivedFrom': 'ADF'}
peripheral BSEC {}
peripheral BSEC_S {'derivedFrom': 'BSEC'}
peripheral CACHEAXI {}
peripheral CACHEAXI_S {'derivedFrom': 'CACHEAXI'}
peripheral CRC {}
peripheral CRC_S {'derivedFrom': 'CRC'}
peripheral CRYP {}
peripheral CRYP_S {'derivedFrom': 'CRYP'}
peripheral CSI {}
peripheral CSI_S {'derivedFrom': 'CSI'}
peripheral DBGMCU {}
peripheral DBGMCU_S {'derivedFrom': 'DBGMCU'}
peripheral DCMI {}
peripheral DCMI_S {'derivedFrom': 'DCMI'}
peripheral DCMIPP {}
peripheral DCMIPP_S {'derivedFrom': 'DCMIPP'}
peripheral DLYBSD {}
peripheral DLYBSD_S {'derivedFrom': 'DLYBSD'}
peripheral DLYBSD2 {'derivedFrom': 'DLYBSD'}
peripheral DLYBSD2_S {'derivedFrom': 'DLYBSD'}
peripheral DMA2D {}
peripheral DMA2D_S {'derivedFrom': 'DMA2D'}
periph

In [79]:
info = {}

for peri in root:
    periname = peri.find("name").text
    periname_simple = re.sub(r"\d+$", "", periname)
    
    info[periname] = {}
    info[periname]["address"] = int(peri.find("baseAddress").text, base=16)

    if peri.attrib.get("derivedFrom"):
        basename = peri.attrib.get("derivedFrom")
        info[periname]["base"] = basename
        continue

    info[periname]["description"] = get_description(peri)
    regsinfo = {}
    info[periname]["registers"] = regsinfo

    regs = peri.find("registers")
    for reg in regs:
        regname = reg.find("name").text
        regname_simple = re.sub(f"^({periname}_|{periname}|{periname_simple}_|{periname_simple})", "", regname)
        if re.findall(r"^\d", regname_simple):
            regname = regname
        else:
            regname = regname_simple
        regsinfo[regname] = {}
        regsinfo[regname]["description"] = get_description(reg)
        regsinfo[regname]["addressOffset"] = int(reg.find("addressOffset").text, base=16)
        reg_access = reg.find("access")
        if reg_access is None:
            reg_access = ""
        else:
            reg_access = reg_access.text
        regsinfo[regname]["resetValue"] = int(reg.find("resetValue").text, base=16)
        fieldsinfo = {}
        regsinfo[regname]["fields"] = fieldsinfo
        
        fields = reg.find("fields")
        if fields is None:
            continue
        for field in fields:
            finfo = {}
            fname = field.find("name").text
            fieldsinfo[fname] = finfo
            finfo["description"] = get_description(field)
            offset = int(field.find("bitOffset").text)
            width = int(field.find("bitWidth").text)
            finfo["mask"] = (2**width - 1) * 2**offset
            field_access = field.find("access")
            if field_access is None:
                field_access = ""
            else:
                field_access = field_access.text
            finfo["access"] = reg_access + field_access

        toremove = set()
        for fname, finfo in fieldsinfo.items():
            if re.findall(r"(_\d+)+$", fname):
                fname_simple = re.sub(r"(_\d+)+$", "", fname)
                if fname_simple in fieldsinfo:
                    fieldsinfo[fname_simple]["mask"] |= finfo["mask"]
                    toremove.add(fname)
        for fname in toremove:
            fieldsinfo.pop(fname)

    tomerge = {}
    for regname, reginfo in regsinfo.items():
        if re.findall("(_Input|_Output)$", regname):
            regname_simple = re.sub("(_Input|_Output)$", "", regname)
            if regname_simple in tomerge:
                tomerge[regname_simple]["fields"] |= regsinfo[regname]["fields"]
            else:
                tomerge[regname_simple] = copy.deepcopy(regsinfo[regname])
                tomerge[regname_simple]["description"] = re.sub(r"\([^)]*\)", "",
                    tomerge[regname_simple]["description"]).rstrip(" ")
    regsinfo |= tomerge

info

{'ADC1': {'address': 1073881088,
  'description': 'Analog-to-digital converters',
  'registers': {'ISR': {'description': 'ADC interrupt and status register',
    'addressOffset': 0,
    'resetValue': 0,
    'fields': {'ADRDY': {'description': 'ADC ready',
      'mask': 1,
      'access': 'read-write'},
     'EOSMP': {'description': 'End of sampling flag',
      'mask': 2,
      'access': 'read-write'},
     'EOC': {'description': 'End of conversion flag',
      'mask': 4,
      'access': 'read-write'},
     'EOS': {'description': 'End of regular sequence flag',
      'mask': 8,
      'access': 'read-write'},
     'OVR': {'description': 'ADC overrun', 'mask': 16, 'access': 'read-write'},
     'JEOC': {'description': 'Injected channel end of conversion flag',
      'mask': 32,
      'access': 'read-write'},
     'JEOS': {'description': 'Injected channel end of sequence flag',
      'mask': 64,
      'access': 'read-write'},
     'AWD1': {'description': 'Analog watchdog 1 flag',
      'ma

In [80]:
def find_arrays(ls):
    results = set()
    re_last_digits = r"(\d+)(?!.*\d)"

    for s in ls:
        if re.findall(re_last_digits, s):
            n = int(re.findall(re_last_digits, s)[0])
            fmt = re.sub(re_last_digits, "{}", s)
            if fmt not in results and \
                fmt.format("") not in ls and \
                fmt.format(n+1) in ls and\
                fmt != "CR{}":
                results.add(fmt)
    
    return results

In [81]:
secure_prefix = ""
secure_postfix = ""

def is_secure_name(s):
    global secure_prefix, secure_postfix
    if s.startswith("SEC_"):
        secure_prefix = "SEC_"
        return True, s[4:]
    if s.endswith("_S"):
        secure_postfix = "_S"
        return True, s[:-2]
    return False, s

for s in info.keys():
    is_secure_name(s)

def get_secured_name(s):
    if secure_prefix:
        s = secure_prefix + s
    elif secure_postfix:
        s = s + secure_postfix
    else:
        s = "ABCDEFG"
    return s

def get_nonsecured_name(s):
    if secure_prefix:
        s = "NSEC_" + s
    elif secure_postfix:
        s = s + "_NS"
    return s

In [82]:
filename = f"./{model}.py"
if secure:
    filename = f"./{model}_s.py"
f = open(filename, "w")
f.write("from seracc import BitField, RegisterBase, PeripheralBase, Subscriptor\n")
f.write("from seracc import logging, wait_until_equal\n")

45

In [83]:
for periname, periinfo in info.items():

    periname_s = periname
    if secure:
        issec, newname = is_secure_name(periname)
        if issec:
            if newname in info.keys():
                periname_s = newname
        else:
            newname = get_secured_name(periname)
            if newname in info.keys():
                periname_s = get_nonsecured_name(periname)
    print(periname, periname_s)

    if "base" in periinfo:
        f.write(f"""\
{periname_s} = SA_{periinfo["base"]}(0x{periinfo["address"]:08X}, \"{periname}\")
""")
        continue

    peri_class = f"""
class SA_{periname}(PeripheralBase):

    def __init__(self, base, name):
        super().__init__(base, name, \"{periinfo["description"]}\")
"""
    
    for regname, reginfo in periinfo["registers"].items():
        classname = f"{periname}_{regname}"
        offset = reginfo["addressOffset"]
        peri_class += f"""\
        self.{regname} = SA_{classname}(self, 0x{offset:X})
"""
        
        reg_class = f"""
class SA_{classname}(RegisterBase):
    
    def __init__(self, peripheral, offset):
        super().__init__(peripheral, offset, 0x{reginfo["resetValue"]:X}, \"{regname}\", \"{reginfo["description"]}\")
"""
        for fieldname, fieldinfo in reginfo["fields"].items():
            reg_class += f"""\
        self.{fieldname} = BitField(self, 0x{fieldinfo["mask"]:08X}, \"{fieldname}\", \"{fieldinfo["description"]}\")
"""
        
        for format in find_arrays(reginfo["fields"].keys()):
            reg_class += f"""\
        self.{format.format("")} = Subscriptor(self, \"{format}\")
"""
        
        f.write(reg_class)

    for format in find_arrays(periinfo["registers"].keys()):
        peri_class += f"""\
        self.{format.format("")} = Subscriptor(self, \"{format}\")
"""
    
    peri_class += f"""
{periname_s} = SA_{periname}(0x{periinfo["address"]:08X}, \"{periname}\")
"""
    
    f.write(peri_class)

ADC1 ADC1
ADC1_S ADC1_S
ADC2 ADC2
ADC2_S ADC2_S
ADC12 ADC12
ADC12_S ADC12_S
ADF ADF
ADF_S ADF_S
BSEC BSEC
BSEC_S BSEC_S
CACHEAXI CACHEAXI
CACHEAXI_S CACHEAXI_S
CRC CRC
CRC_S CRC_S
CRYP CRYP
CRYP_S CRYP_S
CSI CSI
CSI_S CSI_S
DBGMCU DBGMCU
DBGMCU_S DBGMCU_S
DCMI DCMI
DCMI_S DCMI_S
DCMIPP DCMIPP
DCMIPP_S DCMIPP_S
DLYBSD DLYBSD
DLYBSD_S DLYBSD_S
DLYBSD2 DLYBSD2
DLYBSD2_S DLYBSD2_S
DMA2D DMA2D
DMA2D_S DMA2D_S
DTS DTS
DTS_S DTS_S
ETH ETH
ETH_S ETH_S
EXTI EXTI
EXTI_S EXTI_S
FDCAN1 FDCAN1
FDCAN1_S FDCAN1_S
FDCAN2 FDCAN2
FDCAN2_S FDCAN2_S
FDCAN3 FDCAN3
FDCAN3_S FDCAN3_S
FMC1 FMC1
FMC1_S FMC1_S
GFXMMU GFXMMU
GFXMMU_S GFXMMU_S
GFXTIM GFXTIM
GFXTIM_S GFXTIM_S
GPDMA GPDMA
GPDMA_S GPDMA_S
GPIOA GPIOA
GPIOA_S GPIOA_S
GPIOB GPIOB
GPIOB_S GPIOB_S
GPIOC GPIOC
GPIOC_S GPIOC_S
GPIOD GPIOD
GPIOD_S GPIOD_S
GPIOE GPIOE
GPIOE_S GPIOE_S
GPIOF GPIOF
GPIOF_S GPIOF_S
GPIOG GPIOG
GPIOG_S GPIOG_S
GPIOH GPIOH
GPIOH_S GPIOH_S
GPION GPION
GPION_S GPION_S
GPIOO GPIOO
GPIOO_S GPIOO_S
GPIOP GPIOP
GPIOP_S GPIOP_S
GPIOQ GP

In [84]:
f.close()